# GPIB MEtadata extraction: Selenium NO async

In [1]:
import re
str="asderer"
res=re.split(r'\(\d+\)',str)
[i.replace('\xa0', ' ').strip() for i in res]

['asderer']

## Items: find all metadata etc. form a url

In [34]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.support.wait import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup

from selenium.webdriver.chrome.options import Options
import re
chrome_options = Options()
chrome_options.add_argument("--headless=new") # for Chrome >= 109
driver = webdriver.Chrome(options=chrome_options)
metadata=[]
counting=0

In [4]:
import csv

with open('BOoks_GPIB.csv', 'r', encoding='utf-8') as f:
    writer = csv.reader(f)
    data=list(writer) 


urls=[]
for dat in data[1:]:
    urls.append(dat[1])

In [33]:
counting=0

In [60]:
with open("BAD_URLS.txt","r") as file:
    urls=file.read().splitlines()

In [61]:
import time
start=time.time()
counting=0
metadata=[]
for url in urls[counting:]:
    
    driver.get(url)
    wait = WebDriverWait(driver, 60)
    element = wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'metadata-left')))
    soup = BeautifulSoup(driver.page_source, 'html.parser')
    #number of pages:
    check=soup.find_all(class_='dv-viewport-inner dv-clear')
    if len(check)==0:
        #possibly MULTIVolume edition:
        
        
        metadata.append({"Availability":0})
        counting+=1
        continue 
    else:
        metadata_loc={}
        metadata_loc.update({"Availability":1})
        
    images=check[0].find_all(class_='dv-page')
    number_of_images=len(images)
    metadata_loc.update({"Number_of_Images":number_of_images})
    #what images:
    if number_of_images!=0:
        #for image in images:
        indeces=''
        count=0
        for image in images:
            ind=image["class"][1].split("-")[2]
            if count==len(images)-1:
                indeces+=ind
            else:
                indeces+=ind+', '
            count+=1
        metadata_loc.update({"Images":indeces})
    
    metadat=soup.find(class_='table table-condensed table-striped')
    for dat in metadat.find_all('tr'):
        type=dat.find_all('td')[0].get_text().strip().replace('\n',' ')
        da=dat.find_all('td')[1].get_text().strip().replace('\n',' ').replace('\xa0', ' ')
        
        if type in ['Тип издания','Год издания','Коллекции',"Автор","Заглавие"]:
            if "(" in da:
                paren=[v for v, x in enumerate(da) if x == '('][-1]
                da=da[:paren].strip()
            if type in ['Год издания']:
                da=re.sub('\D', '', da)
                if da!='':
                    da=int(da)
            metadata_loc.update({type:da})
        if type in ['Библиографическое описание']:
            metadata_loc.update({type:da})
        if type in ["Родительское издание"]:
            title=da+soup.find(class_="node-title").get_text().strip().replace('\n',' ').replace('\xa0', ' ')
            metadata_loc.update({"title":title})
    metadata_loc.update({"url":url})        
    metadata.append(metadata_loc)
    
    
    print("Index- ", counting)
    counting+=1
print(time.time()-start)

Index-  0
Index-  1
Index-  2
Index-  3
Index-  4
Index-  5
Index-  6
Index-  7
Index-  8
Index-  9
Index-  10
Index-  11
Index-  12
Index-  13
Index-  14
Index-  15
Index-  16
Index-  17
Index-  18
Index-  19
Index-  20
Index-  21
Index-  22
Index-  23
Index-  24
Index-  25
Index-  26
Index-  27
Index-  28
Index-  29
Index-  30
Index-  31
46.86596632003784


In [62]:
metadata_FULL=metadata

In [64]:
import csv
with open("FULL_BOOKS_NEW.csv","a",encoding="utf-8-sig",newline='') as csvf:
    writer =csv.DictWriter(csvf, delimiter=";",fieldnames= ["Год издания","title","url","Availability","Библиографическое описание","Тип издания",'Коллекции',"Автор","Заглавие","Number_of_Images","Images"])
    for dat in metadata_FULL:
        writer.writerow(dat)

In [9]:
#traverse through the resulting list of dictionaries:
import csv

count=1
for met in metadata:
    met.update({"title":data[count][0],"url":data[count][1]})
    #met.update({"url":urls[count]})
    count+=1


with open('FULL_BOOKS_PART_GPIB.csv', 'w', newline='', encoding="utf-8") as output_file:
    dict_writer = csv.DictWriter(output_file, ["Год издания","title","url","Availability","Библиографическое описание","Тип издания",'Коллекции',"Автор","Заглавие","Number_of_Images","Images"])
    dict_writer.writeheader()
    dict_writer.writerows(metadata)

## sub-items: FOR THOSE THAT ARE AVAILABILITY 0 check nodes-grid -  possibly more volumes?
example:
http://elib.shpl.ru/ru/nodes/93921-lenin-v-i-sochineniya-v-30-tomah-locale-nil-izd-2-e-ispr-i-dop-locale-nil-l-1926
 -> traverse through each not found check for subitems and save those instead!

In [46]:
with open("BAD_URLS.txt","r") as file:
    bad_urls=file.read().splitlines()
metadata_FULL=[]
cout=0

In [29]:
metad={
    'Тип издания':"книжное издание, архивный документ",'Год издания':1788,
    'Коллекции':"",
    "Автор":"Сокольский, Иван",
    "Заглавие":"Кабинетский и купеческий секретарь, напечатанный вместе в одной книге в пользу желающих научиться письменному слогу во всяком роде, или Собрание наилучших и употребительнейших писем о всяких материях и на всякий случай",
    'Библиографическое описание':"Сокольский, Иван. Кабинетский и купеческий секретарь, напечатанный вместе в одной книге в пользу желающих научиться письменному слогу во всяком роде, или Собрание наилучших и употребительнейших писем о всяких материях и на всякий случай : с краткими наставлениями для сочинения оных, и с приобщением писем, касающихся до купеческих дел, расписок, верющих и договорных писем, контрактов и векселей : ч. 1 и 2 / [Иван Сокольский]. -  М. : [тип. Ф. Гипиуса], 1788. - Авт. указан в конце посвящ. - Ч. 2 имеет отд. тит. л. и загл. : Купеческий секретарь, содержащий письма касательно купеческих дел, расписки ... ."
}

In [30]:
import time
start=time.time()
#here is the Main Outline:

for url in bad_urls:
    
    print(str(cout) +" st")
    driver.get(url)
    wait = WebDriverWait(driver, 60)
    try:
        element = wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'metadata-left')))
        soup = BeautifulSoup(driver.page_source, 'html.parser')
    except:
        print("BAD_URL: ", url)
        continue
    
    if len(soup.find_all(class_="nodes-grid"))>0:
        sub_url=[]
        sub_title=[]
        full_tit=soup.find(class_="node-title").get_text().strip()
        for li in soup.find_all(class_="nodes-grid")[0].find_all("li"):
            sub_url.append('http://elib.shpl.ru'+li.find(class_='name').a["href"])
            
            sub_=li.find(class_='name').a.get_text().strip()
            sub_=full_tit[:250-len(sub_)]+" "+sub_
            sub_title.append(sub_)
        meta=process_GPIB_normal(sub_url,sub_title,metadat1=metad)
        if meta==0:
            print("BAD_URL in volume: ", url)
        else:
            #save the metadata:
            metadata_FULL=metadata_FULL+meta
    else:
        full_tit=soup.find(class_="node-title").get_text().strip()
        metadata_FULL.append({"Availability":0,"url":url,"title":full_tit})
        print("NOT MULTIVOLUME: ",url)
    cout+=1
print(time.time()-start)
print(cout)

0 st
3.453634023666382
1


In [25]:
def process_GPIB_normal(urls,titles,metadat1={}):
    metadata=[]
    counting=0
    for url in urls:
        
        driver.get(url)
        wait = WebDriverWait(driver, 60)
        try:
            element = wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'dv-viewport-outer')))
            soup = BeautifulSoup(driver.page_source, 'html.parser')
        except:
            continue
        #number of pages:
        check=soup.find_all(class_='dv-viewport-inner dv-clear')
        if len(check)==0:
            metadata.append({"Availability":0,"url":url,"title":titles[counting]}) 
            counting+=1
            continue
        else:
            metadata_loc={}
            metadata_loc.update({"Availability":1})
            
        images=check[0].find_all(class_='dv-page')
        number_of_images=len(images)
        metadata_loc.update({"Number_of_Images":number_of_images})
        #what images:
        if number_of_images!=0:
            #for image in images:
            indeces=''
            count=0
            for image in images:
                ind=image["class"][1].split("-")[2]
                if count==len(images)-1:
                    indeces+=ind
                else:
                    indeces+=ind+', '
                count+=1
            metadata_loc.update({"Images":indeces})
        """
        metadat=soup.find(class_='table table-condensed table-striped')
        for dat in metadat.find_all('tr'):
            type=dat.find_all('td')[0].get_text().strip().replace('\n',' ')
            da=dat.find_all('td')[1].get_text().strip().replace('\n',' ')
            
            if type in ['Тип издания','Год издания','Коллекции',"Автор","Заглавие"]:
                if "(" in da:
                    paren=[v for v, x in enumerate(da) if x == '('][-1]
                    da=da[:paren].strip()
                if type in ['Год издания']:
                    da=re.sub('\D', '', da)
                    if da!='':
                        da=int(da)
                metadata_loc.update({type:da})
            if type in ['Библиографическое описание']:
                da=clean_string(da)
                metadata_loc.update({type:da})
        """
        metadata_loc.update(metadat1)
        metadata_loc.update({"url":url,"title":titles[counting]})
        metadata.append(metadata_loc)
        counting+=1
        
    if len(metadata)==0:
        return 0
    return metadata

In [7]:
import re
def clean_string(str):
    pattern = r'\xa0'
    s_with_space = re.sub(pattern, ' ', str)
    return s_with_space

In [32]:
import csv
with open("FULL_BOOKS_NEW.csv","a",encoding="utf-8-sig",newline='') as csvf:
    writer =csv.DictWriter(csvf, delimiter=";",fieldnames= ["Год издания","title","url","Availability","Библиографическое описание","Тип издания",'Коллекции',"Автор","Заглавие","Number_of_Images","Images"])
    writer.writerow(metadata_FULL[0])
    writer.writerow(metadata_FULL[1])

In [15]:
with open('FULL_BOOKS_PART_GPIB.csv', 'w', newline='', encoding="utf-8") as output_file:
    dict_writer = csv.DictWriter(output_file, ["Год издания","title","url","Availability","Библиографическое описание","Тип издания",'Коллекции',"Автор","Заглавие","Number_of_Images","Images"])
    dict_writer.writeheader()
    dict_writer.writerow(metadata_FULL[0])
    dict_writer.writerow(metadata_FULL[1])

### sub-subitems (only 200s found - deleted): additional availability 0 chechks 

http://elib.shpl.ru/ru/nodes/31894-trotskiy-l-d-sochineniya-m-l-1924-1927
http://elib.shpl.ru/ru/nodes/33125-sssr-verhovnyy-sovet-zasedaniya-verhovnogo-soveta-sssr-m-1938-1991
_> just add РОДИТЕЛЬСКОЕ ИЗДАНИЕ!

In [ ]:
metad={
    'Тип издания':"книжное издание, архивный документ",'Год издания':1924,
    'Коллекции':"",
    "Автор":"Сокольский, Иван",
    "Заглавие":"Кабинетский и купеческий секретарь, напечатанный вместе в одной книге в пользу желающих научиться письменному слогу во всяком роде, или Собрание наилучших и употребительнейших писем о всяких материях и на всякий случай",
    'Библиографическое описание':"Сокольский, Иван. Кабинетский и купеческий секретарь, напечатанный вместе в одной книге в пользу желающих научиться письменному слогу во всяком роде, или Собрание наилучших и употребительнейших писем о всяких материях и на всякий случай : с краткими наставлениями для сочинения оных, и с приобщением писем, касающихся до купеческих дел, расписок, верющих и договорных писем, контрактов и векселей : ч. 1 и 2 / [Иван Сокольский]. -  М. : [тип. Ф. Гипиуса], 1788. - Авт. указан в конце посвящ. - Ч. 2 имеет отд. тит. л. и загл. : Купеческий секретарь, содержащий письма касательно купеческих дел, расписки ... ."
}

In [ ]:
with open("BAD_URLS.txt","r") as file:
    bad_urls=file.read().splitlines()
metadata_FULL=[]
cout=0

In [ ]:
import time
start=time.time()
#here is the Main Outline:

for url in bad_urls:
    
    print(str(cout) +" st")
    driver.get(url)
    wait = WebDriverWait(driver, 60)
    try:
        element = wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'metadata-left')))
        soup = BeautifulSoup(driver.page_source, 'html.parser')
    except:
        print("BAD_URL: ", url)
        continue
    
    if len(soup.find_all(class_="nodes-grid"))>0:
        sub_url=[]
        sub_title=[]
        full_tit=soup.find(class_="node-title").get_text().strip()
        for li in soup.find_all(class_="nodes-grid")[0].find_all("li"):
            sub_url.append('http://elib.shpl.ru'+li.find(class_='name').a["href"])
            
            sub_=li.find(class_='name').a.get_text().strip()
            sub_=full_tit[:250-len(sub_)]+" "+sub_
            sub_title.append(sub_)
        meta=process_GPIB_normal(sub_url,sub_title,metadat1=metad)
        if meta==0:
            print("BAD_URL in volume: ", url)
        else:
            #save the metadata:
            metadata_FULL=metadata_FULL+meta
    else:
        full_tit=soup.find(class_="node-title").get_text().strip()
        metadata_FULL.append({"Availability":0,"url":url,"title":full_tit})
        print("NOT MULTIVOLUME: ",url)
    cout+=1
print(time.time()-start)
print(cout)

In [ ]:
def process_GPIB_normal(urls,titles,metadat1={}):
    metadata=[]
    counting=0
    for url in urls:
        
        driver.get(url)
        wait = WebDriverWait(driver, 60)
        try:
            element = wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'dv-viewport-outer')))
            soup = BeautifulSoup(driver.page_source, 'html.parser')
        except:
            continue
        #number of pages:
        check=soup.find_all(class_='dv-viewport-inner dv-clear')
        if len(check)==0:
            metadata.append({"Availability":0,"url":url,"title":titles[counting]}) 
            counting+=1
            continue
        else:
            metadata_loc={}
            metadata_loc.update({"Availability":1})
            
        images=check[0].find_all(class_='dv-page')
        number_of_images=len(images)
        metadata_loc.update({"Number_of_Images":number_of_images})
        #what images:
        if number_of_images!=0:
            #for image in images:
            indeces=''
            count=0
            for image in images:
                ind=image["class"][1].split("-")[2]
                if count==len(images)-1:
                    indeces+=ind
                else:
                    indeces+=ind+', '
                count+=1
            metadata_loc.update({"Images":indeces})
        """
        metadat=soup.find(class_='table table-condensed table-striped')
        for dat in metadat.find_all('tr'):
            type=dat.find_all('td')[0].get_text().strip().replace('\n',' ')
            da=dat.find_all('td')[1].get_text().strip().replace('\n',' ')
            
            if type in ['Тип издания','Год издания','Коллекции',"Автор","Заглавие"]:
                if "(" in da:
                    paren=[v for v, x in enumerate(da) if x == '('][-1]
                    da=da[:paren].strip()
                if type in ['Год издания']:
                    da=re.sub('\D', '', da)
                    if da!='':
                        da=int(da)
                metadata_loc.update({type:da})
            if type in ['Библиографическое описание']:
                da=clean_string(da)
                metadata_loc.update({type:da})
        """
        metadata_loc.update(metadat1)
        metadata_loc.update({"url":url,"title":titles[counting]})
        metadata.append(metadata_loc)
        counting+=1
        
    if len(metadata)==0:
        return 0
    return metadata

In [ ]:
import csv
with open("FULL_BOOKS_NEW.csv","a",encoding="utf-8-sig",newline='') as csvf:
    writer =csv.DictWriter(csvf, delimiter=";",fieldnames= ["Год издания","title","url","Availability","Библиографическое описание","Тип издания",'Коллекции',"Автор","Заглавие","Number_of_Images","Images"])
    for dat in metadata_FULL:
        writer.writerow(dat)

# CSV CLEANING:

In [68]:
#change FULL_BOOKS_PART TO BOOKS (on 1)
with open("FULL_BOOKS_PART_GPIB.csv","r",encoding="utf-8") as file:
    redaer=csv.reader(file)
    data_init=list(redaer)
with open("FULL_BOOKS_GPIB.csv","r",encoding="utf-8") as file:
    redaer=csv.reader(file)
    data=list(redaer)


In [69]:
urls_dat=[]
for row in data:
    urls_dat.append(row[2])

In [70]:
len(data)

28924

In [71]:
for init in data_init[1:]:
    if init[2] in urls_dat:
        ind=urls_dat.index(init[2])
        data[ind]=init
    else:
        data.append(init)

In [61]:
data

[['Год издания',
  'title',
  'url',
  'Availability',
  'Библиографическое описание',
  'Тип издания',
  'Коллекции',
  'Автор',
  'Заглавие',
  'Number_of_Images',
  'Images'],
 ['1908',
  '\t  Россия. Переселенческое управление. Годовой отчет по Тобольскому переселенческому району за 1907 г. - СПб., 1908. - (Издания Переселенческого управления ; вып. 45).',
  'http://elib.shpl.ru/ru/nodes/45987-rossiya-pereselencheskoe-upravlenie-godovoy-otchet-po-tobolskomu-pereselencheskomu-rayonu-za-1907-g-spb-1908-izdaniya-pereselencheskogo-upravleniya-vyp-45',
  '1',
  'Россия. Переселенческое управление.\xa0Годовой отчет по Тобольскому переселенческому району за 1907 г. / сост. по данным Энгельфельда. -\xa0СПб., 1908. - 109 с. : табл. - (Издания Переселенческого управления ; вып. 45).',
  'книжное издание, архивный документ',
  'Статистические материалы',
  'Россия. Переселенческое управление',
  'Годовой отчет по Тобольскому переселенческому району за 1907 г.',
  '116',
  '3184546, 3184547, 3

In [72]:
with open("CHANGED_DATA.csv","w",encoding="utf-8", newline="") as file:
    wr=csv.writer(file)
    wr.writerows(data)

### Deleting 0's

In [81]:
with open("FULL_BOOKS_NEW.csv","r",encoding="utf-8-sig") as file:
    wr=csv.reader(file)
    new=list(wr)


In [82]:
new

[['Год издания;title;url;Availability;Библиографическое описание;Тип издания;Коллекции;Автор;Заглавие;Number_of_Images;Images'],
 ['1908;"\t  Россия. Переселенческое управление. Годовой отчет по Тобольскому переселенческому району за 1907 г. - СПб.',
  ' 1908. - (Издания Переселенческого управления ; вып. 45).";http://elib.shpl.ru/ru/nodes/45987-rossiya-pereselencheskoe-upravlenie-godovoy-otchet-po-tobolskomu-pereselencheskomu-rayonu-za-1907-g-spb-1908-izdaniya-pereselencheskogo-upravleniya-vyp-45;1;"Россия. Переселенческое управление.\xa0Годовой отчет по Тобольскому переселенческому району за 1907 г. / сост. по данным Энгельфельда. -\xa0СПб.',
  ' 1908. - 109 с. : табл. - (Издания Переселенческого управления ; вып. 45).";книжное издание',
  ' архивный документ;Статистические материалы;Россия. Переселенческое управление;Годовой отчет по Тобольскому переселенческому району за 1907 г.;116;3184546',
  ' 3184547',
  ' 3184548',
  ' 3184549',
  ' 3184550',
  ' 3184551',
  ' 3184552',
  ' 31

In [76]:
good_new=[]
good_new.append(new[0])
for row in new[1:]:
    if row[3]=="1":
        good_new.append(row)

In [78]:
with open("CHANGED_DATA.csv","w",encoding="utf-8", newline="") as file:
    wr=csv.writer(file)
    wr.writerows(good_new)